# Alphalens Example Tear Sheet

Alphalens is designed to aid in the analysis of "alpha factors," data transformations that are used to predict future price movements of financial instruments. Alpha factors take the form of a single value for each asset on each day. The dimension of these values is not necessarily important. We evaluate an alpha factor by considering daily factor values relative to one another. 

It is important to note the difference between an alpha factor and a trading algorithm. A trading algorithm uses an alpha factor, or combination of alpha factors to generate trades.  Trading algorithms cover execution and risk constraints: the business of turning predictions into profits. Alpha factors, on the other hand, are focused soley on making predictions. This difference in scope lends itself to a difference in the methodologies used to evaluate alpha factors and trading algorithms. Alphalens does not contain analyses of things like transaction costs, capacity, or portfolio construction. Those interested in more implementation specific analyses are encouaged to check out pyfolio (https://github.com/quantopian/pyfolio), a library specifically geared towards the evaluation of trading algorithms. 





In [1]:
import alphalens
import pandas as pd
import numpy as np

# 参数

In [2]:
lookahead_bias_days = 5
start_date = "2019-01-01"
end_date = '2020-07-15'

# 数据

In [3]:
from pathlib import Path

In [4]:
fp_sector = Path('sector.pkl')
fp_pricing = Path('price.pkl')

In [5]:
from zipline.research import get_pricing, get_sector_mappings

In [6]:
if not fp_sector.exists():
    # asset -> sector name
    sector_mappings = get_sector_mappings()
    tickers = np.random.choice(list(sector_mappings.keys()), 100)
    sector_mappings = {k:sector_mappings[k] for k in tickers}
    s = pd.Series(sector_mappings)
    s.to_pickle(str(fp_sector))
    
sector_mappings = pd.read_pickle(str(fp_sector)).to_dict()

In [7]:
if not fp_pricing.exists():
    pricing = get_pricing(sector_mappings.keys(), start_date, end_date, fields='b_close')
    pricing.to_pickle(str(fp_pricing))
    
pricing = pd.read_pickle(str(fp_pricing))

In [8]:
pricing.tail()

四方精创(300468)  华纺股份(600448)  开尔新材(300234)  \
b_close                                                               
2020-07-09 00:00:00+00:00         75.70          6.62         41.14   
2020-07-10 00:00:00+00:00         73.73          6.58         39.59   
2020-07-13 00:00:00+00:00         74.76          6.71         42.39   
2020-07-14 00:00:00+00:00         72.31          6.77         41.86   
2020-07-15 00:00:00+00:00         67.66          6.58         40.00   

                           云天化(600096)  中国核电(601985)  光弘科技(300735)  \
b_close                                                              
2020-07-09 00:00:00+00:00         9.03          4.97         42.06   
2020-07-10 00:00:00+00:00         8.84          4.84         40.29   
2020-07-13 00:00:00+00:00         9.18          4.93         40.76   
2020-07-14 00:00:00+00:00         9.09          4.98         44.83   
2020-07-15 00:00:00+00:00         9.06          4.89         40.34   

                           宇环数控(002903)  优刻得(688158)  火炬电子(603678)  \
b_close                                                              
2020-07-09 00:00:00+00:00         22.73        87.35         87.53   
2020-07-10 00:00:00+00:00         22.03        87.29         86.99   
2020-07-13 00:00:00+00:00         23.10        87.38         86.99   
2020-07-14 00:00:00+00:00         23.22        84.45         82.23   
2020-07-15 00:00:00+00:00         22.12        78.99         79.45   

                           久远银海(002777)  ...  森霸传感(300701)  新劲刚(300629)  \
b_close                                  ...                              
2020-07-09 00:00:00+00:00        120.26  ...         60.17        41.17   
2020-07-10 00:00:00+00:00        119.96  ...         61.84        41.66   
2020-07-13 00:00:00+00:00        122.18  ...         68.03        42.67   
2020-07-14 00:00:00+00:00        118.75  ...         63.36        43.74   
2020-07-15 00:00:00+00:00        116.61  ...         59.37        41.20   

                           昊海生科(688366)  南天信息(000948)  上海雅仕(603329)  \
b_close                                                               
2020-07-09 00:00:00+00:00        107.76         23.48         17.39   
2020-07-10 00:00:00+00:00        120.75         23.51         16.75   
2020-07-13 00:00:00+00:00        140.77         24.44         17.07   
2020-07-14 00:00:00+00:00        138.80         23.53         16.77   
2020-07-15 00:00:00+00:00        128.00         23.32         15.71   

                           安宁股份(002978)  益佰制药(600594)  威创股份(002308)  \
b_close                                                               
2020-07-09 00:00:00+00:00         41.52         84.55         34.19   
2020-07-10 00:00:00+00:00         39.96         82.18         33.80   
2020-07-13 00:00:00+00:00         43.00         84.55         35.57   
2020-07-14 00:00:00+00:00         42.45         88.45         34.84   
2020-07-15 00:00:00+00:00         39.61         83.60         33.97   

                           凯发电气(300407)  中电环保(300172)  
b_close                                                
2020-07-09 00:00:00+00:00         35.24         28.26  
2020-07-10 00:00:00+00:00         34.47         27.72  
2020-07-13 00:00:00+00:00         35.20         28.42  
2020-07-14 00:00:00+00:00         34.91         28.31  
2020-07-15 00:00:00+00:00         34.02         27.67  

[5 rows x 100 columns]

For demonstration purposes we will create a predictive factor. To cheat we will look at future prices to make sure we'll rank high stoks that will perform well and vice versa.

In [9]:
predictive_factor = pricing.pct_change(lookahead_bias_days)
# introduce look-ahead bias and make the factor predictive
predictive_factor = predictive_factor.shift(-lookahead_bias_days)
predictive_factor = predictive_factor.stack()
predictive_factor.index = predictive_factor.index.set_names(['date', 'asset'])

In [10]:
predictive_factor.head()

date                       asset       
2019-01-02 00:00:00+00:00  四方精创(300468)    0.026231
                           华纺股份(600448)    0.022450
                           开尔新材(300234)    0.048661
                           云天化(600096)     0.028302
                           中国核电(601985)    0.023748
dtype: float64

The pricing data passed to alphalens should contain the entry price for the assets so it must reflect the next available price after a factor value was observed at a given timestamp. Those prices must not be used in the calculation of the factor values for that time. Always double check to ensure you are not introducing lookahead bias to your study.

The pricing data must also contain the exit price for the assets, for period 1 the price at the next timestamp will be used, for period 2 the price after 2 timestats will be used and so on.

There are no restrinctions/assumptions on the time frequencies a factor should be computed at and neither on the specific time a factor should be traded (trading at the open vs trading at the close vs intraday trading), it is only required that factor and price DataFrames are properly aligned given the rules above.

In our example, before the trading starts every day, we observe yesterday factor values. The price we pass to alphalens is the next available price after that factor observation: the daily open price that will be used as assets entry price. Also, we are not adding additional prices so the assets exit price will be the following days open prices (how many days depends on 'periods' argument). The retuns computed by Alphalens will therefore based on  assets open prices.

In [11]:
pricing = pricing.iloc[1:]
pricing.head()

四方精创(300468)  华纺股份(600448)  开尔新材(300234)  \
b_close                                                               
2019-01-03 00:00:00+00:00        14.380         5.242        10.730   
2019-01-04 00:00:00+00:00        14.834         5.267        10.933   
2019-01-07 00:00:00+00:00        15.090         5.208        11.230   
2019-01-08 00:00:00+00:00        14.991         5.158        11.175   
2019-01-09 00:00:00+00:00        14.906         5.283        11.120   

                           云天化(600096)  中国核电(601985)  光弘科技(300735)  \
b_close                                                              
2019-01-03 00:00:00+00:00         8.48         5.400         8.377   
2019-01-04 00:00:00+00:00         8.65         5.459         8.570   
2019-01-07 00:00:00+00:00         8.77         5.567         8.982   
2019-01-08 00:00:00+00:00         8.72         5.547         9.315   
2019-01-09 00:00:00+00:00         8.72         5.518         9.100   

                           宇环数控(002903)  优刻得(688158)  火炬电子(603678)  \
b_close                                                              
2019-01-03 00:00:00+00:00        25.266          NaN        39.083   
2019-01-04 00:00:00+00:00        25.465          NaN        40.604   
2019-01-07 00:00:00+00:00        25.822          NaN        43.044   
2019-01-08 00:00:00+00:00        25.961          NaN        41.809   
2019-01-09 00:00:00+00:00        25.822          NaN        41.661   

                           久远银海(002777)  ...  森霸传感(300701)  新劲刚(300629)  \
b_close                                  ...                              
2019-01-03 00:00:00+00:00        25.795  ...        20.482       23.736   
2019-01-04 00:00:00+00:00        27.123  ...        21.140       24.106   
2019-01-07 00:00:00+00:00        27.475  ...        21.620       26.524   
2019-01-08 00:00:00+00:00        27.291  ...        21.357       27.044   
2019-01-09 00:00:00+00:00        28.023  ...        21.383       25.855   

                           昊海生科(688366)  南天信息(000948)  上海雅仕(603329)  \
b_close                                                               
2019-01-03 00:00:00+00:00           NaN         8.934        15.200   
2019-01-04 00:00:00+00:00           NaN         9.387        15.466   
2019-01-07 00:00:00+00:00           NaN         9.525        15.732   
2019-01-08 00:00:00+00:00           NaN         9.448        15.683   
2019-01-09 00:00:00+00:00           NaN         9.448        15.722   

                           安宁股份(002978)  益佰制药(600594)  威创股份(002308)  \
b_close                                                               
2019-01-03 00:00:00+00:00           NaN        58.343         19.37   
2019-01-04 00:00:00+00:00           NaN        60.053         20.02   
2019-01-07 00:00:00+00:00           NaN        60.898         20.45   
2019-01-08 00:00:00+00:00           NaN        60.898         21.32   
2019-01-09 00:00:00+00:00           NaN        60.689         20.84   

                           凯发电气(300407)  中电环保(300172)  
b_close                                                
2019-01-03 00:00:00+00:00        28.927        26.960  
2019-01-04 00:00:00+00:00        30.899        27.637  
2019-01-07 00:00:00+00:00        31.785        28.207  
2019-01-08 00:00:00+00:00        32.104        28.158  
2019-01-09 00:00:00+00:00        31.337        28.108  

[5 rows x 100 columns]

Often, we'd want to know how our factor looks across various groupings (sectors, industires, countries, etc.), in this example let's use sectors. To generate sector level breakdowns, you'll need to pass alphalens a sector mapping for each traded name. 

This mapping can come in the form of a MultiIndexed Series (with the same date/symbol index as your factor value) if you want to provide a sector mapping for each symbol on each day. 

If you'd like to use constant sector mappings, you may pass symbol to sector mappings as a dict.

If your sector mappings come in the form of codes (as they do in this tutorial), you may also pass alphalens a dict of sector names to use in place of sector codes.

## Formatting input data

Alphalens contains a handy data formatting function to transform your factor and pricing data into the exact inputs expected by the tear sheet functions.

In [12]:
factor_data = alphalens.utils.get_clean_factor_and_forward_returns(predictive_factor, 
                                                                   pricing, 
                                                                   quantiles=5,
                                                                   bins=None,
                                                                   groupby=sector_mappings)

Dropped 1.7% entries from factor data: 1.7% in forward returns computation and 0.0% in binning phase (set max_loss=0 to see potentially suppressed Exceptions).
max_loss is 35.0%, not exceeded: OK!


The function inform the user how much data was dropped after formatting the input data. Factor data can be partially dropped due to being flawed itself (e.g. NaNs), not having provided enough price data to compute forward returns for all factor values, or because it is not possible to perform binning. It is possible to control the maximum allowed data loss using 'max_loss' argument.

In [13]:
factor_data.head()

1D        5D       10D  \
date                      asset                                        
2019-01-03 00:00:00+00:00 四方精创(300468)  0.031572  0.040264  0.051669   
                          华纺股份(600448)  0.004769 -0.003243  0.041206   
                          开尔新材(300234)  0.018919  0.031221  0.032805   
                          云天化(600096)   0.020047  0.029481  0.084906   
                          中国核电(601985)  0.010926  0.020000  0.009074   

                                          factor group  factor_quantile  
date                      asset                                          
2019-01-03 00:00:00+00:00 四方精创(300468)  0.040264  工程技术                3  
                          华纺股份(600448) -0.003243  可选消费                1  
                          开尔新材(300234)  0.031221  工业领域                2  
                          云天化(600096)   0.029481  基本材料                2  
                          中国核电(601985)  0.020000  公用事业                2

You'll notice that we've placed all of the information we need for our calculations into one dataframe. Variables are the columns, and observations are each row.

The integer columns represents the forward returns or the daily price change for the N days after a timestamp. The 1 day forward return for AAPL on 2014-12-2 is the percent change in the AAPL open price on 2014-12-2 and the AAPL open price on 2014-12-3. The 5 day forward return is the percent change from open 2014-12-2 to open 2014-12-9 (5 trading days) divided by 5.

# Returns Analysis

Returns analysis gives us a raw description of a factor's value that shows us the power of a factor in real currency values.

One of the most basic ways to look at a factor's predicitve power is to look at the mean return of different factor quantile. 

In [14]:
mean_return_by_q_daily, std_err = alphalens.performance.mean_return_by_quantile(factor_data, by_date=True)

In [15]:
mean_return_by_q_daily.head()

1D        5D       10D
factor_quantile date                                                   
1               2019-01-03 00:00:00+00:00 -0.007312 -0.053810 -0.059754
                2019-01-04 00:00:00+00:00 -0.021048 -0.071959 -0.067117
                2019-01-07 00:00:00+00:00 -0.012599 -0.061822 -0.059461
                2019-01-08 00:00:00+00:00 -0.009253 -0.054533 -0.065007
                2019-01-09 00:00:00+00:00 -0.007134 -0.051258 -0.061876

In [16]:
mean_return_by_q, std_err_by_q = alphalens.performance.mean_return_by_quantile(factor_data, by_date=False)

In [17]:
mean_return_by_q.head()

1D        5D       10D
factor_quantile                              
1               -0.014117 -0.063433 -0.064532
2               -0.005125 -0.026307 -0.025564
3               -0.000638 -0.008691 -0.006963
4                0.003944  0.012194  0.014969
5                0.016107  0.086781  0.082710

In [18]:
alphalens.plotting.plot_quantile_returns_bar(mean_return_by_q);

By looking at the mean return by quantile we can get a real look at how well the factor differentiates forward returns across the signal values. Obviously we want securities with a better signal to exhibit higher returns. For a good factor we'd expect to see negative values in the lower quartiles and positive values in the upper quantiles.

In [19]:
alphalens.plotting.plot_quantile_returns_violin(mean_return_by_q_daily);

This violin plot is similar to the one before it but shows more information about the underlying data. It gives a better idea about the range of values, the median, and the inter-quartile range. What gives the plots their shape is the application of a probability density of the data at different values.

In [20]:
quant_return_spread, std_err_spread = alphalens.performance.compute_mean_returns_spread(mean_return_by_q_daily,
                                                                                        upper_quant=5,
                                                                                        lower_quant=1,
                                                                                        std_err=std_err)

In [21]:
alphalens.plotting.plot_mean_quantile_returns_spread_time_series(quant_return_spread, std_err_spread);

This rolling forward returns spread graph allows us to look at the raw spread in basis points between the top and bottom quantiles over time. The green line is the returns spread while the orange line is a 1 month average to smooth the data and make it easier to visualize.

In [22]:
alphalens.plotting.plot_cumulative_returns_by_quantile(mean_return_by_q_daily, period='1D')

By looking at the cumulative returns by factor quantile we can get an intuition for which quantiles are contributing the most to the factor and at what time. Ideally we would like to see a these curves originate at the same value on the left and spread out like a fan as they move to the right through time, with the higher quantiles on the top.

In [23]:
ls_factor_returns = alphalens.performance.factor_returns(factor_data)

In [24]:
ls_factor_returns.head()

1D        5D       10D
date                                                   
2019-01-03 00:00:00+00:00  0.006139  0.090077  0.059574
2019-01-04 00:00:00+00:00  0.014649  0.091779  0.066847
2019-01-07 00:00:00+00:00  0.015618  0.075327  0.081404
2019-01-08 00:00:00+00:00  0.009956  0.072838  0.098608
2019-01-09 00:00:00+00:00  0.011091  0.058449  0.095829

In [25]:
alphalens.plotting.plot_cumulative_returns(ls_factor_returns['1D'], period='1D')

While looking at quantiles is important we must also look at the factor returns as a whole. The cumulative factor long/short returns plot lets us view the combined effects overtime of our entire factor.

In [26]:
alpha_beta = alphalens.performance.factor_alpha_beta(factor_data)

In [27]:
alpha_beta

1D          5D       10D
Ann. alpha  119.747799  119.014475  9.698622
beta          0.046741    0.354503  0.239557

A very important part of factor returns analysis is determing the alpha, and how significant it is. Here we surface the annualized alpha, and beta.

## Returns Tear Sheet

We can view all returns analysis calculations together.

In [28]:
alphalens.tears.create_returns_tear_sheet(factor_data)

# Information Analysis

Information Analysis is a way for us to evaluate the predicitive value of a factor without the confounding effects of transaction costs. The main way we look at this is through the Information Coefficient (IC).

From Wikipedia...

>The information coefficient (IC) is a measure of the merit of a predicted value. In finance, the information coefficient is used as a performance metric for the predictive skill of a financial analyst. The information coefficient is similar to correlation in that it can be seen to measure the linear relationship between two random variables, e.g. predicted stock returns and the actualized returns. The information coefficient ranges from 0 to 1, with 0 denoting no linear relationship between predictions and actual values (poor forecasting skills) and 1 denoting a perfect linear relationship (good forecasting skills).

In [29]:
ic = alphalens.performance.factor_information_coefficient(factor_data)

In [30]:
ic.head()

1D   5D       10D
date                                              
2019-01-03 00:00:00+00:00  0.339973  1.0  0.684508
2019-01-04 00:00:00+00:00  0.514964  1.0  0.670872
2019-01-07 00:00:00+00:00  0.461673  1.0  0.656900
2019-01-08 00:00:00+00:00  0.426419  1.0  0.650471
2019-01-09 00:00:00+00:00  0.392567  1.0  0.523138

In [31]:
alphalens.plotting.plot_ic_ts(ic);

By looking at the IC each day we can understand how theoretically predicitive our factor is overtime. We like our mean IC to be high and the standard deviation, or volatility of it, to be low. We want to find consistently predictive factors.

In [32]:
alphalens.plotting.plot_ic_hist(ic);

Looking at a histogram of the daily IC values can indicate how the factor behaves most of the time, where the likely IC values will fall, it also allows us to see if the factor has fat tails.

In [33]:
alphalens.plotting.plot_ic_qq(ic);

These Q-Q plots show the difference in shape between the distribution of IC values and a normal distribution. This is especially helpful in seeing how the most extreme values in the distribution affect the predicitive power.

In [34]:
mean_monthly_ic = alphalens.performance.mean_information_coefficient(factor_data, by_time='M')

In [35]:
mean_monthly_ic.head()

1D   5D       10D
date                                              
2019-01-31 00:00:00+00:00  0.432011  1.0  0.684845
2019-02-28 00:00:00+00:00  0.406376  1.0  0.630746
2019-03-31 00:00:00+00:00  0.410796  1.0  0.665101
2019-04-30 00:00:00+00:00  0.401171  1.0  0.652273
2019-05-31 00:00:00+00:00  0.403647  1.0  0.654222

In [36]:
alphalens.plotting.plot_monthly_ic_heatmap(mean_monthly_ic);

By displaying the IC data in heatmap format we can get an idea about the consistency of the factor, and how it behaves during different market regimes/seasons.

## Information Tear Sheet

We can view all information analysis calculations together.

In [37]:
alphalens.tears.create_information_tear_sheet(factor_data)

# Turnover Analysis

Turnover Analysis gives us an idea about the nature of a factor's makeup and how it changes.

In [38]:
quantile_factor = factor_data['factor_quantile']
turnover_period = 1

In [39]:
quantile_turnover = pd.concat([alphalens.performance.quantile_turnover(quantile_factor, q, turnover_period)
                               for q in range(1, int(quantile_factor.max()) + 1)], axis=1)

In [40]:
quantile_turnover.head()

1         2         3         4         5
date                                                                       
2019-01-03 00:00:00+00:00       NaN       NaN       NaN       NaN       NaN
2019-01-04 00:00:00+00:00  0.277778  0.555556  0.823529  0.722222  0.500000
2019-01-07 00:00:00+00:00  0.388889  0.722222  0.588235  0.611111  0.333333
2019-01-08 00:00:00+00:00  0.333333  0.555556  0.705882  0.500000  0.166667
2019-01-09 00:00:00+00:00  0.277778  0.666667  0.705882  0.666667  0.222222

In [41]:
alphalens.plotting.plot_top_bottom_quantile_turnover(quantile_turnover, turnover_period)

Factor turnover is important as it indicates the incorporation of new information and the make up of the extremes of a signal. By looking at the new additions to the sets of top and bottom quantiles we can see how much of this factor is getting remade everyday.

In [42]:
factor_autocorrelation = alphalens.performance.factor_rank_autocorrelation(factor_data, turnover_period)

In [43]:
factor_autocorrelation.head()

date
2019-01-03 00:00:00+00:00         NaN
2019-01-04 00:00:00+00:00    0.744484
2019-01-07 00:00:00+00:00    0.689491
2019-01-08 00:00:00+00:00    0.747547
2019-01-09 00:00:00+00:00    0.699666
Name: 1, dtype: float64

In [44]:
alphalens.plotting.plot_factor_rank_auto_correlation(factor_autocorrelation);

The autocorrelation of the factor indicates to us the persistence of the signal itself.

## Turnover Tear Sheet

We can view all turnover calculations together.

In [45]:
alphalens.tears.create_turnover_tear_sheet(factor_data)

# Event Style Returns Analysis

Looking at the average cumulative return in a window before and after a factor can indicate to us how long the predicative power of a factor lasts. This tear sheet takes a while to run.

**NOTE:** This tear sheet takes in an extra argument `pricing`.

In [46]:
alphalens.tears.create_event_returns_tear_sheet(factor_data, pricing, by_group=True)

# Groupwise

Many of the plots in Alphalens can be viewed on their own by grouping if grouping information is provided. The returns and information tear sheets can be viewed groupwise by passing in the `by_group=True` argument.

In [47]:
ic_by_sector = alphalens.performance.mean_information_coefficient(factor_data, by_group=True)

In [48]:
ic_by_sector.head()

1D   5D       10D
group                         
主要消费   0.355556  1.0  0.523546
公用事业   0.325590  1.0  0.590851
医疗保健   0.399520  1.0  0.612834
可选消费   0.395967  1.0  0.639572
基本材料   0.381998  1.0  0.602331

In [49]:
alphalens.plotting.plot_ic_by_group(ic_by_sector);

In [50]:
mean_return_quantile_sector, mean_return_quantile_sector_err = alphalens.performance.mean_return_by_quantile(factor_data, by_group=True)

In [51]:
mean_return_quantile_sector.head()

1D        5D       10D
factor_quantile group                              
1               主要消费  -0.014847 -0.062929 -0.072861
                公用事业  -0.011648 -0.049829 -0.056379
                医疗保健  -0.015230 -0.066418 -0.072564
                可选消费  -0.013751 -0.064248 -0.066020
                基本材料  -0.014249 -0.061924 -0.061173

In [52]:
alphalens.plotting.plot_quantile_returns_bar(mean_return_quantile_sector, by_group=True);

# Summary Tear Sheet

There are a lot of plots above. If you want a quick snapshot of how the alpha factor performs consider the summary tear sheet.

In [53]:
alphalens.tears.create_summary_tear_sheet(factor_data)

# The Whole Thing

If you want to see all of the results create a full tear sheet. By passing in the factor data you can analyze all of the above statistics and plots at once.

In [54]:
alphalens.tears.create_full_tear_sheet(factor_data)